# Make a copy of this notebook!
## Right-click on the file & select 'Duplicate'

In [101]:
open Ppx_stage
open Printf
open Jupyter_notebook

let printf x = kfprintf flush stdout x

let timeit ?(loops = 1_000_000) f =
  let t = Unix.gettimeofday () in 
  for _ = 0 to loops do
      f ();
  done;
  let t' = Unix.gettimeofday () in 
  sprintf "%.4f us/iter" (t' -. t)

module Staged_97988427 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end


module Staged_642947120 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end


module Staged_595357922 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end


val printf : ('a, out_channel, unit, unit) format4 -> 'a = <fun>


val timeit : ?loops:int -> (unit -> 'a) -> string = <fun>


# Multi-stage Programming

This demo will introduce you to metaprogramming using "program staging".

## What is Metaprogramming?

Metaprogramming is a broad topic. 
It includes any programming technique that treats other programs as data to be manipulated or that modifies the behavior of a programming environment.
The following techniques all fall under the umbrella of metaprogramming:
 - Macros
 - Metaobject protocols
 - Templates
 - Multi-stage programming

Macros, templates, and multi-stage programming are all methods for *code generation*; metaobjects are more about changing the semantics of a language from within that language.

Code generation is a useful tool to have in your toolbox.
It can allow you to write applications in a high-level style while getting low-level performance.
For example, many machine learning frameworks rely on a form of code generation to build computation graphs that can be efficiently executed on the GPU.

However, code generation has a well-earned reputation for complexity.
Bugs now have multiple different layers of code to hide in, and it's easy to generate code that looks right but contains some subtle error.
The PL community has developed several ways of making metaprogramming safer, one of which is multi-stage programming.

## Who uses Program Generation, and Why?

Program generation is widely used for performance, generality, and ease of maintenence.
A few common use cases:
 - C++ uses templates for generating generic collections.
 - Go (and many other languages) use code generation for creating pretty-printers & serializers for user-defined data types.
 - 

## What is Multi-stage Programming?

Multi-stage programming is a form of metaprogramming that focuses on type-safe code generation.
As the name suggests, a multi-stage program executes in a sequence of stages.
Each stage generates a *new* program that is executed at the subsequent stage.

This is similar to the way that macros run and produce code before that code is executed.
The key difference between a multi-stage program and a program that uses macros is: a well-typed multi-stage program always generates (1) syntactically valid and (2) well-typed code.

This is a powerful property!
Many macro and template systems ensure that code is syntactically well-formed (in Lisp for example, it just needs to be a s-expression), but few can ensure that it is well-typed.
While being well-typed does not mean that a program is correct, being able to prove that our code generators only produce well-typed programs rules out large classes of bugs.

## Building Blocks of Multi-stage Programming

Multi-stage programming requires only a few language changes.
We add three new constructs:
- Quote
- Unquote
- Eval
- Persist

### Quote
Quoting allows us to *delay* a computation.
The following computes 1 + 2:

In [102]:
let a = 1 + 2

val a : int = 3


By wrapping the computation in a quote, we delay the computation, producing a value of type `int code` instead of a value of type `int`. 

In [103]:
let a = [%code 1 + 2]

val a : int Ppx_stage.code = let _ = 1 + 2


(`Ppx_stage` is the library that provides the staging constructs.)

We can think of a value of type `int code` as a computation that we can run later, which will produce an `int`.
This computation is represented by a program, specifically `1 + 2`.

Quoting allows us to construct code in a type-safe way.
In particular, if we try to mix staged and unstaged computations together, we get an error:

In [104]:
[%code 1] + 2

error: compile_error

### Unquote

Quoting by itself is not that useful, but it becomes much more powerful when we add unquote.
Unquote allows us to build code out of smaller pieces by letting us splice those pieces together.


For example, here we create a new computation that multiplies two smaller computations together:

In [6]:
let a = [%code 1 + 2]
let b = [%code [%e a] * [% e a]]

val a : int Ppx_stage.code = let _ = 1 + 2


val b : int Ppx_stage.code = let _ = (1 + 2) * (1 + 2)


The unquoting operation (written `[%e a]`) evaluates `a` to produce an `int code` value, then splices that code into the overall quotation.

### Eval

We'd like to be able to run our computations.
We can run a computation with the following function:

In [7]:
let run : 'a code -> 'a = run

val run : 'a Ppx_stage.code -> 'a = <fun>


In [8]:
printf "a = %d\n" (run a);
printf "b = %d\n" (run b)

a = 3
b = 9


- : unit = ()


### Persist

Finally, we'd like to able *persist* values from one stage to another.
For example, if we have an `int` value, we'd like to be able to get an `int code`.

For value types like `int` or `bool`, this is straightforward.
Values of these types can be translated into literals and spliced into the resulting code.
More complex types, like functions, ref cells, or file handles, are problematic.
After all, what should it mean to persist an open file handle?
If we persist a reference to some function `func`, we have to make sure that when the generated code is executed, `func` means the same thing that it meant during code generation, or we could violate our type safety guarantee.

For this tutorial, we'll ignore some of these issues, and only consider persisting value types, using the following functions:
 - `Lift.int : int -> int code`
 - `Lift.bool : bool -> bool code`
 - `Lift.string : string -> string code`

In [9]:
(* Problem 1:

How should we add the staging operators (quote, unquote, and 
persist) to the following code so that it evaluates to the 
computation 1 + 2?
*)

let a = (5 - 4) + (2 * 1)

val a : int = 3


## A Classic Example

One common use case for staging in generic programs is to remove the overhead of parameters that change rarely.
The following function computes exponents by repeated squaring.
However, even if we call it many times with the same value of `n`, it has to do some work to figure out how many times to call `square`.

In [10]:
let square x = x * x

let rec power n x =
    if n = 0 then 1
    else if n mod 2 = 0 then square (power (n / 2) x)
    else x * (power (n - 1) x)
    
let result = power 3 4 (* 4 ^ 3 *)

val square : int -> int = <fun>


module Staged_424983024 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val power : int -> int -> int = <fun>


val result : int = 64


In [11]:
let power7 x = power 7 x
let _ = timeit (fun () -> power7 5)

val power7 : int -> int = <fun>


- : string = "0.1722 us/iter"


We should be able to use multi-stage programming to *specialize* `power` to a particular argument `n`, reducing some overhead.
The signature of `power` is `int -> int -> int`.
If we create a new staged power function `spower` that takes a constant `n`, what should its signature be?

We start writing `spower` by introducing the staging constructs:

In [12]:
let rec spower = fun n x ->
  if n = 0 then [%code 1]
  else if n mod 2 = 0 then square (spower (n/2) x)
  else x * (spower (n-1) x)

error: compile_error

In [13]:
let rec spower = fun n x ->
  if n = 0 then [%code 1]
  else if n mod 2 = 0 then [%code square [%e (spower (n/2) x)]]
  else x * (spower (n-1) x)

error: compile_error

In [14]:
let rec spower = fun n x ->
  if n = 0 then [%code 1]
  else if n mod 2 = 0 then [%code square [%e (spower (n/2) x)]]
  else [%code [%e x] * [%e (spower (n-1) x)]]

module Staged_588508760 :
  sig
    val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t
    val staged1 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged2 : int Ppx_stage.code -> int Ppx_stage.code
    val staged3 : int Ppx_stage.code
  end
val spower : int -> int Ppx_stage.code -> int Ppx_stage.code = <fun>


This function is *close*, but we really want something of type `int -> (int -> int) code`.
We can write that function as follows:

In [15]:
let spowern n = [%code fun x -> [%e spower n [%code x]]]

val spowern : int -> (int -> int) Ppx_stage.code = <fun>


Calling the final version of `spowern`, we get code that implements "raise to the power of 7".

In [16]:
spowern 7

- : (int -> int) Ppx_stage.code =
let _ = fun x -> x * (square (x * (square (x * 1))))


In [17]:
let spower7 = fun x -> x * (square (x * (square (x * 1))))

let _ = timeit (fun () -> spower7 5)

val spower7 : int -> int = <fun>


- : string = "0.0294 us/iter"


In [18]:
(* 
Problem 2: Using this staged version of square, write `sspower` so that it 
does not generate code that refers to the `square` function. 
*)

let ssquare x = [%code [%e x] * [%e x]]

(* begin_solution *)
let rec sspower = fun n x ->
  if n = 0 then [%code 1]
  else if n mod 2 = 0 then ssquare (sspower (n/2) x)
  else [%code [%e x] * [%e (sspower (n-1) x)]]
(* end_solution *)
  
let sspowern n = [%code fun x -> [%e sspower n [%code x]]]

let _ = sspowern 7

val ssquare : int Ppx_stage.code -> int Ppx_stage.code = <fun>


module Staged_334122405 :
  sig
    val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t
    val staged1 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged2 : int Ppx_stage.code
  end
val sspower : int -> int Ppx_stage.code -> int Ppx_stage.code = <fun>


val sspowern : int -> (int -> int) Ppx_stage.code = <fun>


- : (int -> int) Ppx_stage.code =
let _ = fun x -> x * ((x * ((x * 1) * (x * 1))) * (x * ((x * 1) * (x * 1))))


In [19]:
(* 
Problem 3: Time your generated function. Does removing the call to square help?
*)

(* begin_solution *)
let sspower7 = fun x -> x * ((x * ((x * 1) * (x * 1))) * (x * ((x * 1) * (x * 1))))
(* end_solution *)

let _ = timeit (fun () -> sspower7 5)

val sspower7 : int -> int = <fun>


- : string = "0.0306 us/iter"


In [20]:
(* 
Problem 3: Modify `sspower` so that it does not generate trivial 1 * x 
multiplications. Copy and time the resulting function.
*)

(* begin_solution *)
let rec sspower = fun n x ->
  if n = 1 then [%code [%e x]]
  else if n mod 2 = 0 then ssquare (sspower (n/2) x)
  else [%code [%e x] * [%e (sspower (n-1) x)]]
  
let sspowern n = [%code fun x -> [%e sspower n [%code x]]]

let sspower7 = fun x -> x * ((x * (x * x)) * (x * (x * x)))

let _ = timeit (fun () -> sspower7 5) 
(* end_solution *)

module Staged_763787767 :
  sig
    val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t
    val staged1 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged2 : 'a Ppx_stage.code -> 'a Ppx_stage.code
  end
val sspower : int -> int Ppx_stage.code -> int Ppx_stage.code = <fun>


val sspowern : int -> (int -> int) Ppx_stage.code = <fun>


val sspower7 : int -> int = <fun>


- : string = "0.0249 us/iter"


## Specializing List.map & Friends

Higher order functions are a common tool in functional programming, but their generality can make them expensive.

In [120]:
let rec map : ('a -> 'b) -> 'a list -> 'b list = 
    fun f l -> 
        match l with
        | [] -> []
        | x::xs -> (f x) :: map f xs

let _ = map (fun x -> x + 1) [1;2;3]

let _ = 
    let l = List.init 100 (fun _ -> 0) in 
    timeit (fun () -> map (fun x -> x + 1) l)

module Staged_976224805 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val map : ('a -> 'b) -> 'a list -> 'b list = <fun>


- : int list = [2; 3; 4]


- : string = "1.7961 us/iter"


Can we use staging to build specialized versions of these functions?

Absolutely!

Here's a first attempt:

In [131]:
let smap1 : ('a -> 'b) code -> ('a list -> 'b list) code = 
    fun f -> 
        [%code 
        let rec map = fun l -> 
            match l with
            | [] -> []
            | x::xs -> ([%e f] x) :: map xs
        in 
        map]

let _ = smap1 [%code (fun x -> x + 1)]

val smap1 : ('a -> 'b) Ppx_stage.code -> ('a list -> 'b list) Ppx_stage.code =
  <fun>


- : (int list -> int list) Ppx_stage.code =
let _ =
  let rec map l =
    match l with | [] -> [] | x::xs -> (((fun x -> x + 1)) x) :: (map xs) in
  map


Is there anything wrong or unsatisfying about the function above?

In [134]:
let smap2 : ('a code -> 'b code) -> ('a list -> 'b list) code = 
    fun f -> 
        [%code 
        let rec map = fun l -> 
            match l with
            | [] -> []
            | x::xs -> ([%e f x]) :: map xs
        in 
        map]

let _ = smap2 (fun x -> [%code [%e x] + 1])

val smap2 :
  ('a Ppx_stage.code -> 'b Ppx_stage.code) ->
  ('a list -> 'b list) Ppx_stage.code = <fun>


- : (int list -> int list) Ppx_stage.code =
let _ =
  let rec map l = match l with | [] -> [] | x::xs -> (x + 1) :: (map xs) in
  map


Can you write a version of `filter` that performs the same specialization?

In [137]:
let rec filter : ('a -> bool) -> 'a list -> 'a list = 
    fun f l ->
        match l with
        | [] -> []
        | x::xs -> 
            if f x then x :: (filter f xs) else (filter f xs)
            
(* begin_solution *)
let sfilter : ('a code -> bool code) -> ('a list -> 'a list) code = 
    fun f -> 
        [%code 
        let rec filter = fun l -> 
            match l with
            | [] -> []
            | x::xs -> 
                if [%e f x] then 
                    x :: (filter xs)
                else filter xs
        in 
        filter]

let _ = sfilter (fun x -> [%code [%e x] > 1])
(* end_solution *)

module Staged_831769058 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val filter : ('a -> bool) -> 'a list -> 'a list = <fun>


val sfilter :
  ('a Ppx_stage.code -> bool Ppx_stage.code) ->
  ('a list -> 'a list) Ppx_stage.code = <fun>


- : (int list -> int list) Ppx_stage.code =
let _ =
  let rec filter l =
    match l with
    | [] -> []
    | x::xs -> if x > 1 then x :: (filter xs) else filter xs in
  filter


## Staging Interpreters



### A Naive Interpreter

In [47]:
(* types for environments and binding *)
type 'a env = string -> 'a

(* the empty environment *)
let empty : _ env = fun x -> failwith (sprintf "unbound variable %s" x)

(* bind a value into an environment *)
let bind : 'a env -> string -> 'a -> 'a env = fun ctx x v -> fun x' -> if x = x' then v else ctx x'

(* expressions and expression evaluation *)
type e = 
    | Int of int
    | Var of string
    | App of string * e
    | Ifz of e * e * e
    | Add of e * e
    | Sub of e * e
    | Mul of e * e
    | Div of e * e    
    
let rec eval2 e (venv : int env) (fenv : (int -> int) env) : int = 
    match e with
    | Int x -> x
    | Var v -> venv v
    | App (f, e) -> (fenv f) (eval2 e venv fenv) (* look up function and call *)
    | Ifz (e1, e2, e3) -> 
        if eval2 e1 venv fenv = 0
        then eval2 e2 venv fenv
        else eval2 e3 venv fenv
    | Add (e1, e2) -> (eval2 e1 venv fenv) + (eval2 e2 venv fenv)
    | Sub (e1, e2) -> (eval2 e1 venv fenv) - (eval2 e2 venv fenv)
    | Div (e1, e2) -> (eval2 e1 venv fenv) / (eval2 e2 venv fenv)
    | Mul (e1, e2) -> (eval2 e1 venv fenv) * (eval2 e2 venv fenv)
    
(* 
Programs consist of:

1. A list of function declarations of the form (function name, argument name, body).
2. An expression.
     
The program:    
([("f", "x", body1); ("g", "y", body2)], expr)

is roughly equivalent to the following OCaml:

let rec f x = body1 in 
let rec g y = body2 in
expr
*)
        
type program = (string * string * e) list * e
    
let rec peval2 : program -> int env -> (int -> int) env -> int = 
  fun (decls, expr) venv fenv ->
    match decls with
    | [] -> eval2 expr venv fenv
    | (name, arg, body)::decls ->
        let rec func x = eval2 body (bind venv arg x) (bind fenv name func) in
        peval2 (decls, expr) venv (bind fenv name func)

module Staged_746611085 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
type 'a env = string -> 'a


val empty : 'a env = <fun>


val bind : 'a env -> string -> 'a -> 'a env = <fun>


module Staged_86832447 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
type e =
    Int of int
  | Var of string
  | App of string * e
  | Ifz of e * e * e
  | Add of e * e
  | Sub of e * e
  | Mul of e * e
  | Div of e * e


module Staged_346075011 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val eval1 : e -> int env -> (int -> int) env -> int = <fun>


module Staged_561131774 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
type program = (string * string * e) list * e


module Staged_913360039 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val peval1 : program -> int env -> (int -> int) env -> int = <fun>


Now we write a program so we can test the interpreter. 
We write a simple recursive factorial function.

In [49]:
let factorial = ([
    ("fact", "x", Ifz (Var "x", Int 1, Mul (Var "x", App ("fact", Sub (Var "x", Int 1)))))
], App ("fact", Int 10))

val factorial : (string * string * e) list * e =
  ([("fact", "x",
     Ifz (Var "x", Int 1, Mul (Var "x", App ("fact", Sub (Var "x", Int 1)))))],
   App ("fact", Int 10))


Timing this code and the equivalent OCaml shows that there is a significant performance difference between the interpreted and native implementations.

In [55]:
let _ = printf "fact 10 = %d\n" (peval2 factorial empty empty)
let _ = timeit (fun () -> peval2 factorial empty empty)

fact 10 = 3628800


- : unit = ()


- : string = "2.0452 us/iter"


In [57]:
let rec fact x = if x = 0 then 1 else x * fact (x - 1)
let _ = printf "fact 10 = %d\n" (fact 10)
let _ = timeit (fun () -> fact 10)

module Staged_293434665 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val fact : int -> int = <fun>


fact 10 = 3628800


- : unit = ()


- : string = "0.1018 us/iter"


### Staging the Interpreter

By modifying the types of `eval` and `peval` and then inserting appropriate staging constructs, we can obtain a staged version.
The staged version produces OCaml code rather than interpreting the input program.
This transformation eliminates the overhead of our interpreter.

If we examine the generated code for this example, it is exactly what we wrote by hand.

In [105]:
let rec eval2 e (venv : int code env) (fenv : (int -> int) code env) : int code = 
    match e with
    | Int x -> Lift.int x
    | Var v -> venv v
    | App (f, e) -> [%code [%e fenv f] [%e eval2 e venv fenv]] (* look up function and call *)
    | Ifz (e1, e2, e3) -> 
        [%code 
            if [%e eval2 e1 venv fenv] = 0
            then [%e eval2 e2 venv fenv]
            else [%e eval2 e3 venv fenv]]
    | Add (e1, e2) -> [%code [%e eval2 e1 venv fenv] + [%e eval2 e2 venv fenv]]
    | Sub (e1, e2) -> [%code [%e eval2 e1 venv fenv] - [%e eval2 e2 venv fenv]]
    | Div (e1, e2) -> [%code [%e eval2 e1 venv fenv] / [%e eval2 e2 venv fenv]]
    | Mul (e1, e2) -> [%code [%e eval2 e1 venv fenv] * [%e eval2 e2 venv fenv]]
            
let rec peval2 : program -> int code env -> (int -> int) code env -> int code = 
  fun (decls, expr) venv fenv ->
    match decls with
    | [] -> eval2 expr venv fenv
    | (name, arg, body)::decls ->
        [%code 
            let rec func x = 
                [%e eval2 body (bind venv arg [%code x]) 
                               (bind fenv name [%code func])]
            in
            [%e peval2 (decls, expr) venv (bind fenv name func)]]

module Staged_25971579 :
  sig
    val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t
    val staged1 :
      'a Ppx_stage.code -> ('a -> 'b) Ppx_stage.code -> 'b Ppx_stage.code
    val staged2 :
      'a Ppx_stage.code ->
      'a Ppx_stage.code -> int Ppx_stage.code -> 'a Ppx_stage.code
    val staged3 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged4 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged5 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged6 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
  end
val eval2 :
  e ->
  int Ppx_stage.code env ->
  (int -> int) Ppx_stage.code env -> int Ppx_stage.code = <fun>


module Staged_1009613694 :
  sig
    val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t
    val staged1 :
      (('a -> 'b) Ppx_stage.code -> 'c Ppx_stage.code) ->
      ('a Ppx_stage.code -> ('a -> 'b) Ppx_stage.code -> 'b Ppx_stage.code) ->
      'c Ppx_stage.code
    val staged2 : 'a Ppx_stage.code -> 'b Ppx_stage.code -> 'b Ppx_stage.code
    val staged3 : 'a Ppx_stage.code -> 'b Ppx_stage.code -> 'a Ppx_stage.code
  end
val peval2 :
  program ->
  int Ppx_stage.code env ->
  (int -> int) Ppx_stage.code env -> int Ppx_stage.code = <fun>


In [106]:
peval2 factorial empty empty

- : int Ppx_stage.code =
let _ = let rec func x = if x = 0 then 1 else x * (func (x - 1)) in func 10


### Optimizing the Generated Code with Inlining

While we can eliminate the overhead of intepretation, it would be even more impressive if we could *optimize* the generated code.
In this example, we show that we can apply an inlining/unrolling transformation through a clever use of the staging constructs.

First, we introduce a helper function `repeat` that takes an integer `n`, a function `f`, and a value `x`, and applies `f` `n` times to `x`. For example, `repeat 3 f x = f (f (f x))`.

Next, we replace the part of `peval` that generates function declarations. In the original, a function declaration produces a recursive let-binding. 

In the modified version, function declarations still produce recursive lets, but when the body of the function is produced, it gets a special context. In the normal function context, when a function is called it produces a direct call to that function. In the new version, when a function is called it produces an inlined copy of that function's body.

In [113]:
let rec repeat : int -> ('a -> 'a) -> 'a -> 'a = 
  fun n f -> 
    if n = 0 then f else
        fun x -> f (repeat (n - 1) f x)

let rec eval3 e (venv : int code env) (fenv : (int code -> int code) env) : int code = 
    match e with
    | Int x -> Lift.int x
    | Var v -> venv v
    | App (f, e) -> fenv f (eval3 e venv fenv) (* look up function and call *)
    | Ifz (e1, e2, e3) -> 
        [%code 
            if [%e eval3 e1 venv fenv] = 0
            then [%e eval3 e2 venv fenv]
            else [%e eval3 e3 venv fenv]]
    | Add (e1, e2) -> [%code [%e eval3 e1 venv fenv] + [%e eval3 e2 venv fenv]]
    | Sub (e1, e2) -> [%code [%e eval3 e1 venv fenv] - [%e eval3 e2 venv fenv]]
    | Div (e1, e2) -> [%code [%e eval3 e1 venv fenv] / [%e eval3 e2 venv fenv]]
    | Mul (e1, e2) -> [%code [%e eval3 e1 venv fenv] * [%e eval3 e2 venv fenv]]

let rec peval3 : program -> int code env -> (int code -> int code) env -> int code = 
  fun (decls, expr) venv fenv ->
    match decls with
    | [] -> eval3 expr venv fenv
    | (name, arg, body)::decls ->
        [%code 
            let rec func x = 
                [%e 
                    let emit_body cf x = 
                        eval3 body (bind venv arg x) (bind fenv name cf)
                    in
                    repeat 1 emit_body (fun y -> [%code func [%e y]]) [%code x]] 
            in
            [%e peval3 (decls, expr) venv (bind fenv name (fun y -> [%code func [%e y]]))]]

module Staged_695620909 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val repeat : int -> ('a -> 'a) -> 'a -> 'a = <fun>


module Staged_217817597 :
  sig
    val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t
    val staged1 :
      'a Ppx_stage.code ->
      'a Ppx_stage.code -> int Ppx_stage.code -> 'a Ppx_stage.code
    val staged2 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged3 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged4 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
    val staged5 :
      int Ppx_stage.code -> int Ppx_stage.code -> int Ppx_stage.code
  end
val eval3 :
  e ->
  int Ppx_stage.code env ->
  (int Ppx_stage.code -> int Ppx_stage.code) env -> int Ppx_stage.code =
  <fun>


module Staged_823571339 :
  sig
    val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t
    val staged1 :
      (('a -> 'b) Ppx_stage.code -> 'c Ppx_stage.code) ->
      ('a Ppx_stage.code -> ('a -> 'b) Ppx_stage.code -> 'b Ppx_stage.code) ->
      'c Ppx_stage.code
    val staged2 :
      ('a -> 'b) Ppx_stage.code -> 'a Ppx_stage.code -> 'b Ppx_stage.code
    val staged3 :
      ('a -> 'b) Ppx_stage.code ->
      'c Ppx_stage.code -> 'a Ppx_stage.code -> 'b Ppx_stage.code
    val staged4 : 'a Ppx_stage.code -> 'b Ppx_stage.code -> 'b Ppx_stage.code
  end
val peval3 :
  program ->
  int Ppx_stage.code env ->
  (int Ppx_stage.code -> int Ppx_stage.code) env -> int Ppx_stage.code =
  <fun>


In [112]:
peval3 factorial empty empty

- : int Ppx_stage.code =
let _ =
  let rec func x =
    if x = 0
    then 1
    else x * (if (x - 1) = 0 then 1 else (x - 1) * (func ((x - 1) - 1))) in
  func 10


In [100]:
let rec func x =
    if x = 0
    then 1
    else
      x *
        (if (x - 1) = 0
         then 1
         else
           (x - 1) *
             (if ((x - 1) - 1) = 0
              then 1
              else ((x - 1) - 1) * (func (((x - 1) - 1) - 1))))
              
let _ = timeit (fun () -> func 10)

module Staged_526156727 :
  sig val modcontext''_ : 'a Ppx_stage.Internal.StrMap.t end
val func : int -> int = <fun>


- : string = "0.0708 us/iter"


# References
- "A Gentle Introduction to Multi-stage Programming", Walid Taha